# Introduction & Preparation

Author: Nina Ezhelenko (nina.ezhelenko@deliveryhero.com) & Yuzhu Zhang (yuzhu.zhang@deliveryhero.com)

In [ ]:
# load packages
#from autoplotter import run_app # Importing the autoplotter for GUI Based EDA
from datetime import datetime, timedelta, time, date
from scipy import stats
import json
import os
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from pandas.io import gbq
from google.cloud import bigquery
import plotly.offline as pyo
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import scipy.stats
#import geopandas
from shapely import wkt
import scipy
from scipy import signal
from google.colab import files
%matplotlib inline
from google.colab import drive # to allow colab save file in my drive
drive.mount('/content/drive')
from google.colab import auth
auth.authenticate_user()
import gspread
from oauth2client.client import GoogleCredentials
gc = gspread.authorize(GoogleCredentials.get_application_default())
print('Authenticated')
cwd=os.getcwd()
cwd
%unload_ext google.colab.data_table

Mounted at /content/drive
Authenticated
The google.colab.data_table extension is not loaded.


## Specify Gsheet link for excluded vendor list

In [ ]:
# specify working directory where all documents are saved 
%cd "/content/drive/Shared drives/Global Pricing/2 - Entities/Europe/RO Foodpanda/5 - AB testing/Surge test Q1 2021"
%pwd
#%ls

# Please copy paste the link for excluded vendors' list
wb = gc.open_by_url('https://docs.google.com/spreadsheets/d/1nGWvH66AFQl9YJAQ4SQw1FiGEoEZu0HLxkV3ruUNLnU/edit#gid=0')
sheet = wb.worksheet('Sheet1')
data = sheet.get_all_values()
excluded = pd.DataFrame(data)
excluded.columns = excluded.iloc[0]
excluded=excluded.iloc[1:]
excluded.head()

/content/drive/Shared drives/Global Pricing/2 - Entities/Europe/RO Foodpanda/5 - AB testing/Surge test Q1 2021


0 vendor_code in_test
1        v3nm   FALSE
2        v3sh   FALSE
3        a6aj   FALSE
4        a6ns   FALSE
5        b0nu   FALSE

In [ ]:
# define a few things (project id, start date etc.)
#project_id = "fulfillment-dwh-production"
project_id = "logistics-data-staging-flat" #free
#fulfillment-dwh-production
client = bigquery.Client(project = project_id)
entity_id = 'FP_RO'
country_code = 'ro'
vat_rate = 0.19
start_date = '2021-01-27'
end_date = '2021-03-14'
pre_date = '2021-01-01'
time_zone = "Europe/Bucharest"
#excluded_vendors = ""
# to check delay data
# Run this in BQ to check timezone for a city: SELECT cc.timezone FROM fulfillment-dwh-production.cl.countries c JOIN unnest(cities) as cc WHERE cc.name='Oradea'
zone_id = "32" #,30,44
#city_name = "Pitesti" # the spelling should be the same as in the excel file (MP vendors data from central DWH)  'Jonkoping', 'Frolunda'

# define Accounts that had different settings (chain ID's)
# to do so, run this in BQ: SELECT v.vendor_code, chain.id FROM fulfillment-dwh-production.cl.vendors_v2 v WHERE entity_id='FP_RO' AND v.vendor_code in ('v4mr','v7uo')
KA = ["cw1gf"]

fleet_delay1 = 8.5
fleet_delay2 = 12.5

# trunc time function
def ceil_dt(dt, delta):
    return dt + (datetime.min - dt) % delta

# 2. A/B Test Analysis

## User analysis

### a. User amount in control and variantion

#### Total user

In [ ]:
# WARNING: expensive query
query_user_total = """
WITH city_data AS (
  SELECT p.entity_id
    , country_code
    , ci.name AS city_name
    , ci.id AS city_id
    , zo.shape AS zone_shape 
    , zo.name AS zone_name
    , zo.id AS zone_id
  FROM fulfillment-dwh-production.cl.countries co
  LEFT JOIN UNNEST(co.platforms) p
  LEFT JOIN UNNEST(co.cities) ci
  LEFT JOIN UNNEST(ci.zones) zo
  WHERE entity_id = \"""" + entity_id + """\"
  and zo.id in (""" + zone_id + """)
)
 
SELECT  
customer.variant
, count(distinct customer.user_id) as user_count
, count(distinct customer.session.id) as session_count
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) between \"""" + start_date + """\" and \"""" + end_date + """\"
and created_date >= \"""" + start_date + """\" 
and s.entity_id = \"""" + entity_id + """\"
and customer.variant in ("Variation1", "Control")
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1

    """

user_total = client.query(query_user_total).to_dataframe()
user_total

variant  user_count  session_count
0     Control       16221         111082
1  Variation1       16092         113227

In [ ]:
# calculate user amt per segment
user_Control_r = user_total.loc[user_total['variant'] == 'Control'].reset_index()
user_Control = user_Control_r['user_count'][0]
user_Variation1_r = user_total.loc[user_total['variant'] == 'Variation1'].reset_index()
user_Variation1 = user_Variation1_r['user_count'][0]
user_delta_V1_vs_C = user_Variation1/user_Control-1
user_adj_factor_V1 = user_Control/user_Variation1

print(user_Control, user_Variation1, user_delta_V1_vs_C)

16221 16092 -0.00795265396707967


#### Daily User

In [ ]:
# Pre-condition check
# WARNING: expensive query
query_user = """
WITH city_data AS (
  SELECT p.entity_id
    , country_code
    , ci.name AS city_name
    , ci.id AS city_id
    , zo.shape AS zone_shape 
    , zo.name AS zone_name
    , zo.id AS zone_id
  FROM fulfillment-dwh-production.cl.countries co
  LEFT JOIN UNNEST(co.platforms) p
  LEFT JOIN UNNEST(co.cities) ci
  LEFT JOIN UNNEST(ci.zones) zo
  WHERE entity_id = \"""" + entity_id + """\"
  and zo.id in (""" + zone_id + """)
)
 
SELECT  
cast(DATETIME(created_at, \"""" + time_zone + """\") as date) as local_date
--, extract(hour from created_at) as hour
, customer.variant
, count(distinct customer.user_id) as user_count
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) between \"""" + start_date + """\" and \"""" + end_date + """\"
and created_date >= \"""" + start_date + """\" 
and s.entity_id = \"""" + entity_id + """\"
and customer.variant in ("Variation1", "Control")
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1,2

    """

user = client.query(query_user).to_dataframe()
user.head()

local_date  variant  user_count
0  2021-03-08  Control        1992
1  2021-02-27  Control        1461
2  2021-01-28  Control        1441
3  2021-02-22  Control        1459
4  2021-02-03  Control        1492

In [ ]:
fig = px.line(user.sort_values('local_date'), x="local_date", y="user_count", color = "variant", 
              height=500, width=1200, category_orders = {
                                 "variant": ["Control", "Variation1"]},
              title="Daily user count across testing period")
fig.update_yaxes(showticklabels=True)

for axis in fig.layout:
    if type(fig.layout[axis]) == go.layout.YAxis:
        fig.layout[axis].title.text = ''

fig.show()

#### Hourly user

In [ ]:
# Pre-condition check
# WARNING: expensive query
query_user = """
WITH city_data AS (
  SELECT p.entity_id
    , country_code
    , ci.name AS city_name
    , ci.id AS city_id
    , zo.shape AS zone_shape 
    , zo.name AS zone_name
    , zo.id AS zone_id
  FROM fulfillment-dwh-production.cl.countries co
  LEFT JOIN UNNEST(co.platforms) p
  LEFT JOIN UNNEST(co.cities) ci
  LEFT JOIN UNNEST(ci.zones) zo
  WHERE entity_id = \"""" + entity_id + """\"
  and zo.id in (""" + zone_id + """)
)
 
SELECT  
extract(hour from DATETIME(created_at, \"""" + time_zone + """\")) as hour
, customer.variant
, count(distinct customer.id) as user_count
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) between \"""" + start_date + """\" and \"""" + end_date + """\"
and created_date >= \"""" + start_date + """\" 
and s.entity_id = \"""" + entity_id + """\"
and customer.variant in ("Variation1", "Control")
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1,2

    """

user_hour = client.query(query_user).to_dataframe()

In [ ]:
# display users per hour of day
user_group_h = user_hour.pivot_table("user_count", index=["hour"], columns ="variant", aggfunc = "sum")
user_group_h = user_group_h.reset_index()
user_group_h["control_pp"] = user_group_h["Control"]/user_group_h["Control"].sum()
user_group_h["variation1_pp"] = user_group_h["Variation1"]/user_group_h["Variation1"].sum()
user_group_h["delta"] = user_group_h["Variation1"]/user_group_h["Control"]-1

fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =user_group_h.hour, y=user_group_h.control_pp, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =user_group_h.hour, y=user_group_h.variation1_pp, name ="variation1"), secondary_y=False)

# Add figure title
fig.update_layout(title_text="Hourly users in Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Hour")
# Set y-axes titles
fig.update_yaxes(title_text="Hourly user share", showgrid=False, secondary_y=False)
fig.show()

#### Significance check

In [ ]:
# create dataframe of daily user comparison
user_group = user.pivot_table("user_count", index=["local_date"], columns ="variant", aggfunc = "sum").reset_index()

signif_user_amt_v1 = stats.wilcoxon(user_group['Variation1'], user_group['Control'], alternative='two-sided') 

alpha = 0.05
if (signif_user_amt_v1[0] != 0) & (signif_user_amt_v1[1] <= alpha):
    print ("reject null hypothesis, mean of {} is different from the mean of {}".format('Variation1','Control'))
else:
    print ("do not reject null hypothesis")

do not reject null hypothesis


In [ ]:
print(signif_user_amt_v1)

WilcoxonResult(statistic=452.5, pvalue=0.238002885707977)


### b. User location in control and variantion

In [ ]:
# Pre-condition check
query_location = """
WITH city_data AS (
  SELECT p.entity_id
    , country_code
    , ci.name AS city_name
    , ci.id AS city_id
    , zo.shape AS zone_shape 
    , zo.name AS zone_name
    , zo.id AS zone_id
  FROM fulfillment-dwh-production.cl.countries co
  LEFT JOIN UNNEST(co.platforms) p
  LEFT JOIN UNNEST(co.cities) ci
  LEFT JOIN UNNEST(ci.zones) zo
  WHERE entity_id = \"""" + entity_id + """\"
  and zo.id in (""" + zone_id + """)
)
 
SELECT  
st_x(customer.location) as lon
,st_y(customer.location) as lat
-- st_x(ST_GEOGPOINTFROMGEOHASH(st_geohash(customer.location, 7))) as lon
--, st_y(ST_GEOGPOINTFROMGEOHASH(st_geohash(customer.location, 7))) as lat
, customer.variant
, count(distinct customer.id) as user_count
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) between \"""" + start_date + """\" and \"""" + end_date + """\"
and created_date >= \"""" + start_date + """\" 
and s.entity_id = \"""" + entity_id + """\"
and customer.variant in ("Variation1", "Control")
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1,2,3

    """

location = client.query(query_location).to_dataframe()
location.head()

lon        lat  variant  user_count
0  26.901080  46.573393  Control           3
1  26.902359  46.554180  Control           9
2  26.901805  46.572754  Control           1
3  26.920629  46.560099  Control           1
4  26.903361  46.572251  Control           3

In [ ]:
# Visualize user locations (Control vs Test)
location_Control = location[location['variant']=='Control']

map = px.scatter_mapbox(location_Control, lat="lat", lon="lon", hover_name="variant", hover_data=["user_count"], color="variant", size="user_count", opacity=0.15, 
                        color_discrete_map={"Variation1": "blue",
                                            "Control": "red"
                                            },
                        zoom=11, height=500
                        )
map.update_layout(mapbox_style="open-street-map")
map.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
map.show()

In [ ]:
# Visualize user locations (Control vs Test)
location_Variation = location[location['variant']=='Variation1']

map = px.scatter_mapbox(location_Variation, lat="lat", lon="lon", hover_name="variant", hover_data=["user_count"], color="variant", size="user_count", opacity=0.15, 
                        color_discrete_map={"Variation1": "blue",
                                            "Control": "red"
                                            },
                        zoom=11, height=500
                        )
map.update_layout(mapbox_style="open-street-map")
map.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
map.show()

### c. Users by visit frequency (test)




In [ ]:
# WARNING: expensive query
query_user_freq = """
WITH city_data AS (
  SELECT p.entity_id
    , country_code
    , ci.name AS city_name
    , ci.id AS city_id
    , zo.shape AS zone_shape 
    , zo.name AS zone_name
    , zo.id AS zone_id
  FROM fulfillment-dwh-production.cl.countries co
  LEFT JOIN UNNEST(co.platforms) p
  LEFT JOIN UNNEST(co.cities) ci
  LEFT JOIN UNNEST(ci.zones) zo
  WHERE entity_id = \"""" + entity_id + """\"
  and zo.id in (""" + zone_id + """)
),
 
user_data as
(SELECT  
customer.variant
, customer.user_id
, count(distinct customer.session.id) as session_count
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) between \"""" + start_date + """\" and \"""" + end_date + """\"
and created_date >= \"""" + start_date + """\" 
and s.entity_id = \"""" + entity_id + """\"
and customer.variant in ("Variation1", "Control")
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1,2)

SELECT 
session_count,
count (case when variant="Control" then user_id END) as Control_users
,count (case when variant="Variation1" then user_id END) as Variation1_users
--,count (case when variant="Variation2" then user_id END) as Variation2_users
FROM user_data
GROUP BY 1
ORDER BY 1

    """

user_freq = client.query(query_user_freq).to_dataframe()
user_freq

session_count  Control_users  Variation1_users
0                1           4580              4594
1                2           2469              2392
2                3           1591              1519
3                4           1120              1138
4                5            898               844
..             ...            ...               ...
123            182              1                 0
124            209              2                 0
125            211              0                 1
126            287              1                 0
127            462              0                 1

[128 rows x 3 columns]

In [ ]:
user_freq_limit = user_freq[user_freq.session_count<=50]

fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =user_freq_limit.session_count, y=user_freq_limit.Control_users, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =user_freq_limit.session_count, y=user_freq_limit.Variation1_users, name ="variation1"), secondary_y=False)

# Add figure title
fig.update_layout(title_text="Visit frequency in Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="nr_sessions")
# Set y-axes titles
fig.update_yaxes(title_text="nr users", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
user_total['avg_session_per_user'] = user_total['session_count']/user_total['user_count']
user_total

variant  user_count  session_count  avg_session_per_user
0     Control       16221         111082              6.848036
1  Variation1       16092         113227              7.036229

### d. Users by visit frequency (before test)

In [ ]:
# WARNING: expensive query
query_user_freq_b = """
WITH city_data AS (
  SELECT p.entity_id
    , country_code
    , ci.name AS city_name
    , ci.id AS city_id
    , zo.shape AS zone_shape 
    , zo.name AS zone_name
    , zo.id AS zone_id
  FROM fulfillment-dwh-production.cl.countries co
  LEFT JOIN UNNEST(co.platforms) p
  LEFT JOIN UNNEST(co.cities) ci
  LEFT JOIN UNNEST(ci.zones) zo
  WHERE entity_id = \"""" + entity_id + """\"
  and zo.id in (""" + zone_id + """)
),
 
user_data as
(SELECT  
customer.variant
, customer.user_id
, count(distinct customer.session.id) as session_count
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) between \"""" + start_date + """\" and \"""" + end_date + """\"
and created_date >= \"""" + start_date + """\" 
and s.entity_id = \"""" + entity_id + """\"
and customer.variant in ("Variation1", "Control")
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1,2
),

user_data_b as
(SELECT  
customer.user_id
, count(distinct customer.session.id) as session_count
, min(DATETIME(created_at, \"""" + time_zone + """\")) as first_session_pre
FROM `fulfillment-dwh-production.cl.dynamic_pricing_user_sessions` s
left join city_data cd ON s.entity_id = cd.entity_id
WHERE cast(DATETIME(created_at, \"""" + time_zone + """\") as date) > \"""" + pre_date + """\" 
and cast(DATETIME(created_at, \"""" + time_zone + """\") as date) < \"""" + start_date + """\"
and created_date > \"""" + pre_date + """\"
and s.entity_id = \"""" + entity_id + """\"
and ST_CONTAINS(cd.zone_shape, customer.location) IS TRUE
group by 1
)

SELECT 
ut.variant
, ut.user_id
, ut.session_count as sessions_test
, ub.session_count as sessions_before_test
, ub.first_session_pre

FROM user_data ut
LEFT JOIN user_data_b ub ON ut.user_id=ub.user_id


    """

user_freq_b = client.query(query_user_freq_b).to_dataframe()
user_freq_b.head()

variant  ...          first_session_pre
0  Variation1  ... 2021-01-02 03:01:12.920205
1  Variation1  ... 2021-01-02 17:30:07.564478
2  Variation1  ... 2021-01-02 19:31:58.487529
3  Variation1  ... 2021-01-03 15:18:11.810887
4     Control  ... 2021-01-02 13:08:02.259028

[5 rows x 5 columns]

In [ ]:
## replace nulls with 0
user_freq_b['sessions_before_test'] = user_freq_b['sessions_before_test'].fillna(0)

In [ ]:
df_user_freq_b = user_freq_b.pivot_table(["sessions_test","sessions_before_test"], 
                             index=["variant"], 
                             aggfunc = {"sessions_test": "mean","sessions_before_test":"mean"}).reset_index()
df_user_freq_b

variant  sessions_before_test  sessions_test
0     Control              3.419826       6.848036
1  Variation1              3.490119       7.036229

## Commercial metrics

In [ ]:
query = """
WITH 
costs as (
  select
    p.entity_id,
    l.platform_order_code order_code,
    sum(p.delivery_costs) delivery_costs,
  from 
    (select
      entity_id,
      country_code,
      created_date,
      order_id,
      delivery_costs,
      row_number() over(partition by entity_id, order_id order by created_date desc) as rank
    from fulfillment-dwh-production.cl.utr_timings) p
  left join fulfillment-dwh-production.cl.orders l on p.order_id = l.order_id and p.country_code = l.country_code
  where p.entity_id = \"""" + entity_id + """\"
    and rank = 1
  group by 1,2),

city_data as (
    select
          p.entity_id
        , co.country_code
        , ci.name city_name
        , ci.id city_id
        , zo.shape zone_shape
        , zo.id zone_id
        , zo.name zone_name
        , concat(zo.id,'-',zo.name) zone
        , ROW_NUMBER() OVER (PARTITION BY p.entity_id, country_code, ci.id, zo.id ORDER BY zo.zone_shape_updated_at desc) as rn_zone_shape_update
    from fulfillment-dwh-production.cl.countries co
    left join unnest(co.platforms) p
    left join unnest(co.cities) ci
    left join unnest(ci.zones) zo
    where co.country_code = \"""" + country_code + """\"
    and ci.is_active
    and zo.is_active),

vendors as (
select
     v.entity_id
    , city_name 
    , chain.id as chain_id
    , chain.name as chain_name
    , v.vendor_code
    , v.name as vendor_name
    , v.vertical_type
    , zone_id
    , zone_name
from fulfillment-dwh-production.cl.vendors_v2 v
left join city_data cd ON v.entity_id = cd.entity_id and st_contains(cd.zone_shape, v.location)
where v.entity_id = \"""" + entity_id + """\"
  and v.is_active
  and (cd.rn_zone_shape_update=1 OR cd.rn_zone_shape_update is NULL)
group by 1,2,3,4,5,5,6,7,8,9
order by 1,2,3,5)


  SELECT date AS utc_date
    , cast(placed_at_local as date) local_date
    , placed_at_local local_time
    , LOWER(country_iso) AS country_code
    , platform AS operating_system
    , order_code_google AS platform_order_code_ga
    , o.vendor_code
    , v.vertical_type
    , ifnull(od.zone_name, v.zone_name) AS zone_name
    , ifnull(od.zone_id, v.zone_id) as zone_id
    , o.session_id
    , o.perseus_client_id
    , is_own_delivery 
    , COALESCE(variant_transaction, variant_last, variant_first) AS variant
    --, ab_test_id
    , v.chain_id
    , ab_test_variant
    , IF(dps_sessionid_transaction = 'NA' OR dps_sessionid_transaction = '', NULL, dps_sessionid_transaction) AS dps_sessionid_transaction
    , IF(dps_sessionid_first = 'NA' OR dps_sessionid_first = '', NULL, dps_sessionid_first) AS dps_sessionid_first
    , IF(dps_sessionid_last = 'NA'OR dps_sessionid_last = '', NULL, dps_sessionid_last) AS dps_sessionid_last
    , o.gmv_eur
    , o.gfv_eur
    , o.gmv_local
    , o.gfv_local
    , o.delivery_fee_eur
    , o.delivery_fee_eur_accounting
    , o.delivery_fee_local
    , o.delivery_fee_local_accounting
    , co.is_acquisition
    , cast(co.value.commission_local as FLOAT64) as commission_local
    , cast(co.value.delivery_fee_local as FLOAT64) as cen_delivery_fee_local
    , cast(co.value.delivery_fee_vat_local as FLOAT64) as cen_delivery_fee_vat_local
    , cast(co.value.joker_vendor_fee_local as FLOAT64) as cen_joker_vendor_fee_local
    , cast(COALESCE(dps_delivery_fee_transaction, dps_delivery_fee_last, dps_delivery_fee_first) as FLOAT64) AS dps_delivery_fee
    , cast(COALESCE(dps_surge_fee_transaction, dps_surge_fee_last, dps_surge_fee_first) as FLOAT64) AS dps_surge_fee
    , cast(COALESCE(dps_travel_time_transaction, dps_travel_time_last, dps_travel_time_first) as FLOAT64) AS dps_travel_time
    , COALESCE(dps_sessionid_transaction_created_at, dps_sessionid_last_created_at, dps_sessionid_first_created_at) AS dps_sessionid_created_at
    , travel_time_distance_km
    , mean_delay
    , (SELECT stats.mean_delay FROM f.stats ORDER BY created_at DESC LIMIT 1) AS mean_delay_calc
    , travel_time
    , to_customer_time
    , to_vendor_time
    , delivery_distance
    , actual_delivery_time
    , order_delay_mins
    , c.delivery_costs 
  FROM `fulfillment-dwh-production.dl.digital_analytics_dps_sessions_mapped_to_orders` o
  LEFT JOIN `fulfillment-dwh-production.curated_data_shared_central_dwh.orders` co on o.order_code_google = co.order_id and lower(o.country_iso) = LOWER(RIGHT(co.global_entity_id,2))
  LEFT JOIN fulfillment-dwh-production.cl._dps_sessions_mapped_to_orders od on o.order_code_google = od.platform_order_code and LOWER(RIGHT(od.entity_id,2)) = lower(o.country_iso)
  LEFT JOIN costs c on lower(o.country_iso) = LOWER(RIGHT(c.entity_id,2)) and o.order_code_google = c.order_code
  LEFT JOIN vendors v on lower(o.country_iso) = LOWER(RIGHT(v.entity_id,2)) and o.vendor_code = v.vendor_code
  LEFT JOIN fulfillment-dwh-production.cl.zone_stats f ON LOWER(o.country_iso) = f.country_code AND ifnull(od.zone_id, v.zone_id) = f.zone_id AND TIMESTAMP_TRUNC(co.placed_at, MINUTE) = f.created_at_bucket
  WHERE lower(country_iso) = \"""" + country_code + """\" 
    AND date between \"""" + start_date + """\" and \"""" + end_date + """\"
    AND cast(placed_at_local as date) between DATE_ADD(\"""" + start_date + """\", INTERVAL -2 DAY)  and DATE_ADD(\"""" + end_date + """\", INTERVAL 2 DAY)
    AND is_sent
    AND COALESCE(variant_transaction, variant_last, variant_first) in ("Control", "Variation1")
    AND ifnull(od.zone_id, v.zone_id) in (""" + zone_id + """)
    """

raw = client.query(query).to_dataframe()

In [ ]:
#create a copy of raw data frame
df = raw.copy()

# combining delay values into 1 column
df["mean_fleet_delay"] = df.apply(lambda row: row.mean_delay if pd.isnull(row.mean_delay)==False else row.mean_delay_calc, axis=1)

#fillna with 0
df = df.fillna(0)

# add KA flag
df["KA_flag"] = df.chain_id.isin(KA)

# merge data frame to get excluded vendor info
df = pd.merge(df, excluded, left_on='vendor_code', right_on='vendor_code', how='left')
df["in_test"] = df["in_test"].fillna(True)
df['in_test'] = df['in_test'].replace(['FALSE'], False)

# define delivery type
df["delivery_type"] = df["is_own_delivery"]
df.loc[df.is_own_delivery == True, "delivery_type"] = "OD"
df.loc[df.is_own_delivery == False, "delivery_type"] = "MP"

# create new column "type" for MP, OD_KA, OD_nonKA, OD_excluded
df["type"] = df["delivery_type"]
df.loc[(df.delivery_type == "OD") & (df.KA_flag == True), "type"] = "OD_KA"
df.loc[(df.delivery_type == "OD") & (df.KA_flag == False), "type"] = "OD_nonKA"
df.loc[(df.delivery_type == "OD") & (df.in_test == False), "type"] = "OD_excluded"

# round travel time into 1min buckets
df["tt"] = round(df["travel_time"],0)

# get new time block using 30min interval
df["new_time"] = ceil_dt((df['local_time'].dt.to_pydatetime()), timedelta(minutes=30))
df["new_time"] = df['new_time'].dt.time

# format date 
df.local_date = pd.to_datetime(df.local_date, format='%Y-%m-%d')

# Get net delivery fee
df["rev_delivery_fee_local"] = df["delivery_fee_local"] / (1+vat_rate)
df["DF"] = df["delivery_fee_local"]
df.loc[df.delivery_type == "MP", "DF_rev"] = 0

# define comm rev (not 100% clear if the field includes VAT or not)
df["comm_rev"] = df['commission_local'] ## / (1+vat_rate) # really?

# define revenue
df["rev"] = df["commission_local"]
df.loc[df.delivery_type == "OD", "rev"] = df["rev_delivery_fee_local"] + df["commission_local"] + df["cen_joker_vendor_fee_local"]
df.loc[df.delivery_type == "MP", "rev"] = df["commission_local"] + df["cen_joker_vendor_fee_local"]

# define profit
df["profit"] = df["rev"] -  df["delivery_costs"]

# delete duplicates
df = df.drop_duplicates()

# add a few columns    
df["order"] = df["platform_order_code_ga"]  

In [ ]:
# define stage of the setup (OD)
conditions = [
    (df['mean_fleet_delay'] <= fleet_delay1),
    (df['mean_fleet_delay'] > fleet_delay1) & (df['mean_fleet_delay'] <= fleet_delay2),
    #(df['mean_fleet_delay'] > fleet_delay2) & (df['mean_fleet_delay'] <= fleet_delay3),
    (df['mean_fleet_delay'] > fleet_delay2)
    ]
values = ['default', 'surge1','surge2']
df["stage"] = np.select(conditions,values)
#different stage for control
df["stage_new"] = df["stage"]
#df.loc[(df.variant == "Control") & (df.stage == "negative_surge") , 'stage_new'] = "default"
df.loc[(df.variant == "Control") & (df.stage == "surge1") , 'stage_new'] = "default"
df.loc[(df.variant == "Control") & (df.stage == "surge2") , 'stage_new'] = "default"

In [ ]:
# create a new data frame to drop duplicates (deleting columns like zones, platforms etc.)
df_copy = df[['utc_date', 'local_date', 'local_time', 'country_code',
       'platform_order_code_ga', 'vendor_code',
       'is_own_delivery', 'variant', 'chain_id',
       'mean_fleet_delay','stage','stage_new',
       'gmv_local', 'gfv_local', 'delivery_fee_local',
       'delivery_fee_local_accounting', 'is_acquisition', 'commission_local',
       'cen_delivery_fee_local', 'cen_delivery_fee_vat_local',
       'cen_joker_vendor_fee_local', 
       'travel_time_distance_km', 'travel_time','KA_flag', 'delivery_type',
       'tt', 'new_time', 'rev_delivery_fee_local', 'in_test', 'type', 'DF', "delivery_costs", "profit", "order",
       'comm_rev', 'rev']].drop_duplicates()

df_copy = df_copy.rename(columns={"rev_delivery_fee_local": "DF_rev"})

# create sum columns for graph visualisation
df_copy["rev_sum"] = df_copy["rev"]
df_copy["DF_sum"] = df_copy["DF"]
df_copy["comm_sum"] = df_copy["comm_rev"]
df_copy["profit_sum"] = df_copy["profit"]
df_copy["tt_sum"] = df_copy["travel_time"]
df_copy["costs_sum"] = df_copy["delivery_costs"]
df_copy["gfv_sum"] = df_copy["gfv_local"]

# create separate data frame for MP and OD 
MP = df_copy[df_copy.delivery_type == 'MP']
OD = df_copy[df_copy.delivery_type == 'OD']

df_copy.head()

utc_date local_date          local_time  ... tt_sum costs_sum gfv_sum
0   2021-03-04 2021-03-04 2021-03-04 10:17:45  ...   4.19    10.841    22.0
1   2021-03-04 2021-03-04 2021-03-04 10:17:45  ...   4.19    10.841    22.0
50  2021-02-15 2021-02-15 2021-02-15 14:21:12  ...   1.37     9.857    76.0
54  2021-03-10 2021-03-10 2021-03-10 12:52:19  ...   8.39    13.709    48.1
55  2021-03-10 2021-03-10 2021-03-10 12:52:19  ...   8.39    13.709    48.1

[5 rows x 43 columns]

### All vendors

####Aggregated level

In [ ]:
df_agg = df_copy.pivot_table(["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"], 
                             index=["local_date", "delivery_type", "variant"], 
                             aggfunc = {"order": "count","rev":"sum","DF_rev":"sum","comm_rev":"sum",
                                        "profit":"sum","travel_time":"sum", "DF":"sum", "delivery_costs":"sum"}).reset_index()
df_agg = df_agg.fillna(0)
df_agg["adjust"] = user_adj_factor_V1
df_agg.loc[df_agg.variant == "Control", "adjust"] = 1
df_agg["order"] = df_agg["order"]*df_agg["adjust"]
df_agg["DF_rev"] = df_agg["DF_rev"] * df_agg["adjust"]
df_agg["DF"] = df_agg["DF"] * df_agg["adjust"]
df_agg["comm_rev"] = df_agg["comm_rev"] * df_agg["adjust"]
df_agg["delivery_costs"] = df_agg["delivery_costs"] * df_agg["adjust"]
df_agg["profit"] = df_agg["profit"] * df_agg["adjust"]
df_agg["rev"] = df_agg["rev"] * df_agg["adjust"]
df_agg["travel_time"] = df_agg["travel_time"] * df_agg["adjust"]

df_agg = df_agg.pivot_table(["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"], 
                             index=["local_date", "delivery_type"], columns = "variant" ,
                             aggfunc = {"order": "sum","rev":"sum","DF_rev":"sum","comm_rev":"sum",
                                        "profit":"sum","travel_time":"sum","DF":"sum", "delivery_costs":"sum"}).reset_index()
df_agg = df_agg.fillna(0)
df_agg.head()

local_date delivery_type       DF  ...          rev travel_time             
variant                           Control  ...   Variation1     Control   Variation1
0       2021-01-27            MP    86.72  ...  1733.475733        0.00     0.000000
1       2021-01-27            OD  2406.19  ...  6048.785495     2082.63  1949.533969
2       2021-01-28            MP   116.62  ...  2083.721113        0.00     0.000000
3       2021-01-28            OD  2725.66  ...  6765.165474     2302.73  2037.674924
4       2021-01-29            MP   110.64  ...  2282.320505        0.00     0.000000

[5 rows x 18 columns]

In [ ]:
df_agg_st.to_csv("Bacau_daily.csv")

In [ ]:
# create empty array list
rows_list = []
Variants = ["Variation1"]
metrics = ["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"]
#delivery_types = df_agg.delivery_type.unique().tolist()
delivery_types = ["MP","OD"]
# loop the data for each zone and each stage
for metric in metrics:
  for variant in Variants:
    for delivery_type in delivery_types:
      df_dt = df_agg.loc[df_agg["delivery_type"] == delivery_type]
      # create order level data frames for signif. level calculations for KPI averages
      df_dt_o_Var = df_copy.loc[(df_copy["delivery_type"] == delivery_type)&(df_copy["variant"] == variant)]
      df_dt_o_Control = df_copy.loc[(df_copy["delivery_type"] == delivery_type)&(df_copy["variant"] == "Control")]
      # Metrics for OD 
      if delivery_type == "OD":
        sum_control = round(df_dt[(metric,"Control")].sum(),2)
        sum_variant = round(df_dt[(metric,variant)].sum(),2)
        sum_delta = sum_variant/sum_control-1   
        sum_sig = stats.wilcoxon(df_dt[(metric,variant)], df_dt[(metric,"Control")], alternative='two-sided') [1]
        sum_sig_tf = sum_sig <= 0.05
        if metric != "order":
          avg_control = round((df_dt[(metric,"Control")].sum()/df_dt[("order","Control")].sum()),2)
          avg_variant = round((df_dt[(metric,variant)].sum()/df_dt[("order",variant)].sum()),2)
          avg_delta = avg_variant/avg_control - 1
          # using non-paired test becasue order level data isn't paired
          avg_sig = stats.mannwhitneyu(df_dt_o_Var[metric],df_dt_o_Control[metric], alternative='two-sided')[1]
          #avg_sig = stats.wilcoxon(df_dt[(metric,variant)]/df_dt[("order",variant)],df_dt[(metric,"Control")]/df_dt[("order","Control")], alternative='two-sided')[1]
          avg_sig_tf = avg_sig <= 0.05
        else:
          avg_control = "NA"
          avg_variant = "NA"
          avg_delta= 0
          avg_sig = "NA"
          avg_sig_tf = "NA"
      # Metrics for MP
      else:
        # OD as metrics
        if metric == "order":
          sum_control = df_dt[(metric,"Control")].sum()
          sum_variant = df_dt[(metric,variant)].sum()
          sum_delta = sum_variant/sum_control-1   
          sum_sig = stats.wilcoxon(df_dt[(metric,variant)], df_dt[(metric,"Control")], alternative='two-sided') [1]
          sum_sig_tf = sum_sig <= 0.05
          avg_control = "NA"
          avg_variant = "NA"
          avg_delta=0
          avg_sig = "NA"
          avg_sig_tf = "NA"
        elif metric == "rev" or metric == "comm_rev" or metric == "profit":
          sum_control = df_dt[(metric,"Control")].sum()
          sum_variant = df_dt[(metric,variant)].sum()
          sum_delta = sum_variant/sum_control-1   
          sum_sig = stats.wilcoxon(df_dt[(metric,variant)], df_dt[(metric,"Control")]) [1]/2
          sum_sig_tf = sum_sig <= 0.05
          avg_control = round((df_dt[(metric,"Control")].sum()/df_dt[("order","Control")].sum()),2)
          avg_variant = round((df_dt[(metric,variant)].sum()/df_dt[("order",variant)].sum()),2)
          avg_delta = avg_variant/avg_control - 1
          # using non-paired test becasue order level data isn't paired
          avg_sig = stats.mannwhitneyu(df_dt_o_Var[metric],df_dt_o_Control[metric], alternative='two-sided')[1]
          #avg_sig = stats.wilcoxon(df_dt[(metric,variant)]/df_dt[("order",variant)],df_dt[(metric,"Control")]/df_dt[("order","Control")], alternative='two-sided')[1]
          avg_sig_tf = avg_sig <= 0.05
        else:
          sum_control = "NA"
          sum_variant = "NA"
          sum_delta = 0 
          sum_sig = "NA"
          sum_sig_tf = "NA"
          avg_control = "NA"
          avg_variant = "NA"
          avg_delta=0
          avg_sig = "NA"
          avg_sig_tf = "NA"
      rows_list.append([delivery_type, metric, variant,sum_control, sum_variant,sum_delta,sum_sig,sum_sig_tf,avg_control,avg_variant,avg_delta, avg_sig,avg_sig_tf])
result = pd.DataFrame(rows_list, columns=["delivery_type",'metrics','variant', "sum_control", "sum_variation",'sum_delta','sum_p-value','sum_sig',"avg_control", "avg_variation","avg_delta",'avg_p-value',"avg_sig"])
result['sum_delta'] = result['sum_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
result['avg_delta'] = result['avg_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
result = result.loc[~((result['delivery_type'] == "MP") & (result['metrics'] == "travel_time")),:]
result = result.loc[~((result['delivery_type'] == "MP") & (result['metrics'] == "delivery_costs")),:]
result = result.loc[~((result['delivery_type'] == "MP") & (result['metrics'] == "DF_rev")),:]
result.sort_values(by = ["metrics"])

delivery_type         metrics     variant  ... avg_delta  avg_p-value avg_sig
12            MP              DF  Variation1  ...     0.00%           NA      NA
13            OD              DF  Variation1  ...     0.88%  1.09073e-05    True
5             OD          DF_rev  Variation1  ...     1.05%  1.09073e-05    True
6             MP        comm_rev  Variation1  ...     0.62%     0.817323   False
7             OD        comm_rev  Variation1  ...     0.69%     0.015518    True
15            OD  delivery_costs  Variation1  ...     0.50%    0.0113429    True
0             MP           order  Variation1  ...     0.00%           NA      NA
1             OD           order  Variation1  ...     0.00%           NA      NA
8             MP          profit  Variation1  ...     0.24%     0.950399   False
9             OD          profit  Variation1  ...     1.03%    0.0294017    True
2             MP             rev  Variation1  ...     0.24%     0.950399   False
3             OD             rev  Variation1  ...     0.67%   0.00415081    True
11            OD     travel_time  Variation1  ...     0.79%     0.501474   False

[13 rows x 13 columns]

#### Stage level

In [ ]:
df_agg_st = df_copy.pivot_table(["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"], 
                             index=["local_date", "delivery_type","stage", "variant"], 
                             aggfunc = {"order": "count","rev":"sum","DF_rev":"sum","comm_rev":"sum",
                                        "profit":"sum","travel_time":"sum", "DF":"sum", "delivery_costs":"sum"}).reset_index()
df_agg_st = df_agg_st.fillna(0)
df_agg_st["adjust"] = user_adj_factor_V1
df_agg_st.loc[df_agg_st.variant == "Control", "adjust"] = 1
df_agg_st["order"] = df_agg_st["order"]*df_agg_st["adjust"]
df_agg_st["DF_rev"] = df_agg_st["DF_rev"] * df_agg_st["adjust"]
df_agg_st["DF"] = df_agg_st["DF"] * df_agg_st["adjust"]
df_agg_st["comm_rev"] = df_agg_st["comm_rev"] * df_agg_st["adjust"]
df_agg_st["delivery_costs"] = df_agg_st["delivery_costs"] * df_agg_st["adjust"]
df_agg_st["profit"] = df_agg_st["profit"] * df_agg_st["adjust"]
df_agg_st["rev"] = df_agg_st["rev"] * df_agg_st["adjust"]
df_agg_st["travel_time"] = df_agg_st["travel_time"] * df_agg_st["adjust"]

df_agg_st = df_agg_st.pivot_table(["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"], 
                             index=["local_date", "delivery_type", "stage"], columns = "variant" ,
                             aggfunc = {"order": "sum","rev":"sum","DF_rev":"sum","comm_rev":"sum",
                                        "profit":"sum","travel_time":"sum","DF":"sum", "delivery_costs":"sum"}).reset_index()
df_agg_st = df_agg_st.fillna(0)
df_agg_st.head()

local_date delivery_type    stage  ...          rev travel_time             
variant                                    ...   Variation1     Control   Variation1
0       2021-01-27            MP  default  ...  1637.784735        0.00     0.000000
1       2021-01-27            MP   surge1  ...    95.690997        0.00     0.000000
2       2021-01-27            MP   surge2  ...     0.000000        0.00     0.000000
3       2021-01-27            OD  default  ...  5752.804856     1927.83  1817.544301
4       2021-01-27            OD   surge1  ...   268.948095      136.40   117.897599

[5 rows x 19 columns]

In [ ]:
# create empty array list
rows_list = []
Variants = ["Variation1"]
metrics = ["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"]
#delivery_types = df_agg_st.delivery_type.unique().tolist()
delivery_types = ["MP","OD"]
stages = df_agg_st["stage"].unique().tolist()
# loop the data for each zone and each stage
for metric in metrics:
  for variant in Variants:
    for delivery_type in delivery_types:
      for stage in stages:
        df_dt = df_agg_st.loc[(df_agg_st["delivery_type"] == delivery_type)&(df_agg_st["stage"] == stage)]
        # create order level data frames for signif. level calculations for KPI averages
        df_dt_o_Var = df_copy.loc[(df_copy["delivery_type"] == delivery_type)&(df_copy["stage"] == stage)&(df_copy["variant"] == variant)]
        df_dt_o_Control = df_copy.loc[(df_copy["delivery_type"] == delivery_type)&(df_copy["stage"] == stage)&(df_copy["variant"] == "Control")]
        # Metrics for OD 
        if delivery_type == "OD":
          sum_control = round(df_dt[(metric,"Control")].sum(),2)
          sum_variant = round(df_dt[(metric,variant)].sum(),2)
          sum_delta = sum_variant/sum_control-1   
          sum_sig = stats.wilcoxon(df_dt[(metric,variant)], df_dt[(metric,"Control")], alternative='two-sided') [1]
          sum_sig_tf = sum_sig <= 0.05
          if metric != "order":
            avg_control = round((df_dt[(metric,"Control")].sum()/df_dt[("order","Control")].sum()),2)
            avg_variant = round((df_dt[(metric,variant)].sum()/df_dt[("order",variant)].sum()),2)
            avg_delta = avg_variant/avg_control - 1
            # using non-paired test becasue order level data isn't paired
            avg_sig = stats.mannwhitneyu(df_dt_o_Var[metric],df_dt_o_Control[metric], alternative='two-sided')[1]
            #avg_sig = stats.wilcoxon(df_dt[(metric,variant)]/df_dt[("order",variant)],df_dt[(metric,"Control")]/df_dt[("order","Control")], alternative='two-sided')[1]
            avg_sig_tf = avg_sig <= 0.05
          else:
            avg_control = "NA"
            avg_variant = "NA"
            avg_delta= 0
            avg_sig = "NA"
            avg_sig_tf = "NA"
        # Metrics for MP
        else:
          # OD as metrics
          if metric == "order":
            sum_control = df_dt[(metric,"Control")].sum()
            sum_variant = df_dt[(metric,variant)].sum()
            sum_delta = sum_variant/sum_control-1   
            sum_sig = stats.wilcoxon(df_dt[(metric,variant)], df_dt[(metric,"Control")], alternative='two-sided') [1]
            sum_sig_tf = sum_sig <= 0.05
            avg_control = "NA"
            avg_variant = "NA"
            avg_delta=0
            avg_sig = "NA"
            avg_sig_tf = "NA"
          elif metric == "rev" or metric == "comm_rev" or metric == "profit":
            sum_control = df_dt[(metric,"Control")].sum()
            sum_variant = df_dt[(metric,variant)].sum()
            sum_delta = sum_variant/sum_control-1   
            sum_sig = stats.wilcoxon(df_dt[(metric,variant)], df_dt[(metric,"Control")]) [1]/2
            sum_sig_tf = sum_sig <= 0.05
            avg_control = round((df_dt[(metric,"Control")].sum()/df_dt[("order","Control")].sum()),2)
            avg_variant = round((df_dt[(metric,variant)].sum()/df_dt[("order",variant)].sum()),2)
            avg_delta = avg_variant/avg_control - 1
            # using non-paired test becasue order level data isn't paired
            avg_sig = stats.mannwhitneyu(df_dt_o_Var[metric],df_dt_o_Control[metric], alternative='two-sided')[1]
            #avg_sig = stats.wilcoxon(df_dt[(metric,variant)]/df_dt[("order",variant)],df_dt[(metric,"Control")]/df_dt[("order","Control")], alternative='two-sided')[1]
            avg_sig_tf = avg_sig <= 0.05
          else:
            sum_control = "NA"
            sum_variant = "NA"
            sum_delta = 0 
            sum_sig = "NA"
            sum_sig_tf = "NA"
            avg_control = "NA"
            avg_variant = "NA"
            avg_delta=0
            avg_sig = "NA"
            avg_sig_tf = "NA"
        rows_list.append([delivery_type, stage, metric, variant,sum_control, sum_variant,sum_delta,sum_sig,sum_sig_tf,avg_control,avg_variant,avg_delta, avg_sig,avg_sig_tf])
result = pd.DataFrame(rows_list, columns=["delivery_type","stage",'metrics','variant', "sum_control", "sum_variation",'sum_delta','sum_p-value','sum_sig',"avg_control", "avg_variation","avg_delta",'avg_p-value',"avg_sig"])
result['sum_delta'] = result['sum_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
result['avg_delta'] = result['avg_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
result = result.loc[~((result['delivery_type'] == "MP") & (result['metrics'] == "travel_time")),:]
result = result.loc[~((result['delivery_type'] == "MP") & (result['metrics'] == "delivery_costs")),:]
result = result.loc[~((result['delivery_type'] == "MP") & (result['metrics'] == "DF_rev")),:]
result.sort_values(by = ["metrics"])

delivery_type    stage         metrics  ... avg_delta avg_p-value avg_sig
41            OD   surge2              DF  ...    11.52%  7.4371e-17    True
40            OD   surge1              DF  ...     5.55%  1.8858e-12    True
39            OD  default              DF  ...    -0.53%    0.596965   False
38            MP   surge2              DF  ...     0.00%          NA      NA
37            MP   surge1              DF  ...     0.00%          NA      NA
36            MP  default              DF  ...     0.00%          NA      NA
17            OD   surge2          DF_rev  ...    11.55%  7.4371e-17    True
16            OD   surge1          DF_rev  ...     5.53%  1.8858e-12    True
15            OD  default          DF_rev  ...    -0.63%    0.596965   False
22            OD   surge1        comm_rev  ...    -0.68%    0.719595   False
20            MP   surge2        comm_rev  ...    -0.92%    0.767278   False
23            OD   surge2        comm_rev  ...     0.77%    0.756827   False
18            MP  default        comm_rev  ...     1.00%    0.423297   False
21            OD  default        comm_rev  ...     0.99%   0.0113149    True
19            MP   surge1        comm_rev  ...     0.12%    0.397498   False
46            OD   surge1  delivery_costs  ...     0.61%    0.184002   False
45            OD  default  delivery_costs  ...     0.39%   0.0619156   False
47            OD   surge2  delivery_costs  ...     1.30%    0.601403   False
0             MP  default           order  ...     0.00%          NA      NA
1             MP   surge1           order  ...     0.00%          NA      NA
2             MP   surge2           order  ...     0.00%          NA      NA
3             OD  default           order  ...     0.00%          NA      NA
4             OD   surge1           order  ...     0.00%          NA      NA
5             OD   surge2           order  ...     0.00%          NA      NA
24            MP  default          profit  ...     0.49%    0.520094   False
25            MP   surge1          profit  ...    -0.48%    0.342208   False
26            MP   surge2          profit  ...     0.00%    0.852005   False
27            OD  default          profit  ...     0.21%    0.220516   False
28            OD   surge1          profit  ...     2.88%    0.107752   False
29            OD   surge2          profit  ...     9.14%   0.0215693    True
6             MP  default             rev  ...     0.49%    0.520094   False
10            OD   surge1             rev  ...     1.39%   0.0172657    True
11            OD   surge2             rev  ...     4.33%  0.00615226    True
8             MP   surge2             rev  ...     0.00%    0.852005   False
9             OD  default             rev  ...     0.34%    0.158787   False
7             MP   surge1             rev  ...    -0.48%    0.342208   False
35            OD   surge2     travel_time  ...    -1.01%    0.491792   False
33            OD  default     travel_time  ...     0.99%    0.388489   False
34            OD   surge1     travel_time  ...     0.39%    0.892968   False

[39 rows x 14 columns]

In [ ]:
#default
result.loc[result["stage"] == "default"]

delivery_type    stage         metrics  ... avg_delta avg_p-value avg_sig
0             MP  default           order  ...     0.00%          NA      NA
3             OD  default           order  ...     0.00%          NA      NA
6             MP  default             rev  ...     0.49%    0.520094   False
9             OD  default             rev  ...     0.34%    0.158787   False
15            OD  default          DF_rev  ...    -0.63%    0.596965   False
18            MP  default        comm_rev  ...     1.00%    0.423297   False
21            OD  default        comm_rev  ...     0.99%   0.0113149    True
24            MP  default          profit  ...     0.49%    0.520094   False
27            OD  default          profit  ...     0.21%    0.220516   False
33            OD  default     travel_time  ...     0.99%    0.388489   False
36            MP  default              DF  ...     0.00%          NA      NA
39            OD  default              DF  ...    -0.53%    0.596965   False
45            OD  default  delivery_costs  ...     0.39%   0.0619156   False

[13 rows x 14 columns]

In [ ]:
#surge1
result.loc[result["stage"] == "surge1"]

delivery_type   stage         metrics  ... avg_delta avg_p-value avg_sig
1             MP  surge1           order  ...     0.00%          NA      NA
4             OD  surge1           order  ...     0.00%          NA      NA
7             MP  surge1             rev  ...    -0.48%    0.342208   False
10            OD  surge1             rev  ...     1.39%   0.0172657    True
16            OD  surge1          DF_rev  ...     5.53%  1.8858e-12    True
19            MP  surge1        comm_rev  ...     0.12%    0.397498   False
22            OD  surge1        comm_rev  ...    -0.68%    0.719595   False
25            MP  surge1          profit  ...    -0.48%    0.342208   False
28            OD  surge1          profit  ...     2.88%    0.107752   False
34            OD  surge1     travel_time  ...     0.39%    0.892968   False
37            MP  surge1              DF  ...     0.00%          NA      NA
40            OD  surge1              DF  ...     5.55%  1.8858e-12    True
46            OD  surge1  delivery_costs  ...     0.61%    0.184002   False

[13 rows x 14 columns]

In [ ]:
#surge2
result.loc[result["stage"] == "surge2"]

delivery_type   stage         metrics  ... avg_delta avg_p-value avg_sig
2             MP  surge2           order  ...     0.00%          NA      NA
5             OD  surge2           order  ...     0.00%          NA      NA
8             MP  surge2             rev  ...     0.00%    0.852005   False
11            OD  surge2             rev  ...     4.33%  0.00615226    True
17            OD  surge2          DF_rev  ...    11.55%  7.4371e-17    True
20            MP  surge2        comm_rev  ...    -0.92%    0.767278   False
23            OD  surge2        comm_rev  ...     0.77%    0.756827   False
26            MP  surge2          profit  ...     0.00%    0.852005   False
29            OD  surge2          profit  ...     9.14%   0.0215693    True
35            OD  surge2     travel_time  ...    -1.01%    0.491792   False
38            MP  surge2              DF  ...     0.00%          NA      NA
41            OD  surge2              DF  ...    11.52%  7.4371e-17    True
47            OD  surge2  delivery_costs  ...     1.30%    0.601403   False

[13 rows x 14 columns]

### OD Non-KAs only

In [ ]:
df_sep = OD.pivot_table(["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"], 
                             index=["local_date", "type", "variant"], 
                             aggfunc = {"order": "count","rev":"sum","DF_rev":"sum","comm_rev":"sum",
                                        "profit":"sum","travel_time":"sum", "DF":"sum","delivery_costs":"sum"}).reset_index()
df_sep = df_sep.fillna(0)
df_sep["adjust"] = user_adj_factor_V1
df_sep.loc[df_sep.variant == "Control", "adjust"] = 1
df_sep["order"] = df_sep["order"]*df_sep["adjust"]
df_sep["DF_rev"] = df_sep["DF_rev"] * df_sep["adjust"]
df_sep["DF"] = df_sep["DF"] * df_sep["adjust"]
df_sep["comm_rev"] = df_sep["comm_rev"] * df_sep["adjust"]
df_sep["delivery_costs"] = df_sep["delivery_costs"] * df_sep["adjust"]
df_sep["profit"] = df_sep["profit"] * df_sep["adjust"]
df_sep["rev"] = df_sep["rev"] * df_sep["adjust"]
df_sep["travel_time"] = df_sep["travel_time"] * df_sep["adjust"]

df_sep = df_sep.pivot_table(["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"], 
                             index=["local_date", "type"], columns = "variant" ,
                             aggfunc = {"order": "sum","rev":"sum","DF_rev":"sum","comm_rev":"sum",
                                        "profit":"sum","travel_time":"sum","DF":"sum", "delivery_costs":"sum"}).reset_index()
df_sep = df_sep.fillna(0)
# create separate data frame
OD_KA = df_sep[df_sep[("type",)] == "OD_KA"]
OD_nonKA = df_sep[df_sep[("type",)] == "OD_nonKA"]
OD_excluded = df_sep[df_sep[("type",)] == "OD_excluded"]

/usr/local/lib/python3.7/dist-packages/ipykernel/kernelbase.py:399: PerformanceWarning:

indexing past lexsort depth may impact performance.



In [ ]:
# create empty array list
rows_list = []
Variants = ["Variation1"]
metrics = ["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"]

# loop the data for each zone and each stage
for metric in metrics:
  for variant in Variants:
    # create order level data frames for signif. level calculations for KPI averages
      df_nonKA_o_Var = df_copy.loc[(df_copy["type"] == "OD_nonKA")&(df_copy["variant"] == variant)]
      df_nonKA_o_Control = df_copy.loc[(df_copy["type"] == "OD_nonKA")&(df_copy["variant"] == "Control")]
      sum_control = round(OD_nonKA[(metric,"Control")].sum(),2)
      sum_variant = round(OD_nonKA[(metric,variant)].sum(),2)
      sum_delta = sum_variant/sum_control-1   
      sum_sig = stats.wilcoxon(OD_nonKA[(metric,variant)], OD_nonKA[(metric,"Control")], alternative='two-sided') [1]
      sum_sig_tf = sum_sig <= 0.05
      if metric != "order":
        avg_control = round((OD_nonKA[(metric,"Control")].sum()/OD_nonKA[("order","Control")].sum()),2)
        avg_variant = round((OD_nonKA[(metric,variant)].sum()/OD_nonKA[("order",variant)].sum()),2)
        avg_delta = avg_variant/avg_control - 1
        # using non-paired test becasue order level data isn't paired
        avg_sig = stats.mannwhitneyu(df_nonKA_o_Var[metric],df_nonKA_o_Control[metric], alternative='two-sided')[1]
        #avg_sig = stats.wilcoxon(OD_nonKA[(metric,variant)]/OD_nonKA[("order",variant)],OD_nonKA[(metric,"Control")]/OD_nonKA[("order","Control")], alternative='two-sided')[1]
        avg_sig_tf = avg_sig <= 0.05
      else:
        avg_control = "NA"
        avg_variant = "NA"
        avg_delta= 0
        avg_sig = "NA"
        avg_sig_tf = "NA"
      rows_list.append([metric, variant,sum_control, sum_variant,sum_delta,sum_sig,sum_sig_tf,avg_control,avg_variant,avg_delta, avg_sig, avg_sig_tf])
OD_nonKA_result = pd.DataFrame(rows_list, columns=['metrics','variant', "sum_control", "sum_variation",'sum_delta','sum_p-value','sum_sig',"avg_control", "avg_variation","avg_delta",'avg_p-value',"avg_sig"])
OD_nonKA_result['sum_delta'] = OD_nonKA_result['sum_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
OD_nonKA_result['avg_delta'] = OD_nonKA_result['avg_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
OD_nonKA_result.sort_values(by = ["metrics"])

metrics     variant  sum_control  ...  avg_delta  avg_p-value  avg_sig
6              DF  Variation1     72520.49  ...      1.92%  2.86757e-09     True
2          DF_rev  Variation1     60941.59  ...      1.90%  2.86757e-09     True
3        comm_rev  Variation1    140649.78  ...      0.41%    0.0992807    False
7  delivery_costs  Variation1    117735.60  ...      0.69%    0.0307544     True
0           order  Variation1     11600.00  ...      0.00%           NA       NA
4          profit  Variation1     84740.67  ...      0.68%    0.0553989    False
1             rev  Variation1    202476.27  ...      0.74%    0.0108642     True
5     travel_time  Variation1     55451.93  ...      0.42%     0.787891    False

[8 rows x 12 columns]

### OD KAs only

In [ ]:
# create empty array list
rows_list = []
Variants = ["Variation1"]
metrics = ["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"]

# loop the data for each zone and each stage
for metric in metrics:
  for variant in Variants:
    # create order level data frames for signif. level calculations for KPI averages
      df_KA_o_Var = df_copy.loc[(df_copy["type"] == "OD_KA")&(df_copy["variant"] == variant)]
      df_KA_o_Control = df_copy.loc[(df_copy["type"] == "OD_KA")&(df_copy["variant"] == "Control")]
      sum_control = round(OD_KA[(metric,"Control")].sum(),2)
      sum_variant = round(OD_KA[(metric,variant)].sum(),2)
      sum_delta = sum_variant/sum_control-1   
      sum_sig = stats.wilcoxon(OD_KA[(metric,variant)], OD_KA[(metric,"Control")], alternative='two-sided') [1]
      sum_sig_tf = sum_sig <= 0.05
      if metric != "order":
        avg_control = round((OD_KA[(metric,"Control")].sum()/OD_KA[("order","Control")].sum()),2)
        avg_variant = round((OD_KA[(metric,variant)].sum()/OD_KA[("order",variant)].sum()),2)
        avg_delta = avg_variant/avg_control - 1
        # using non-paired test becasue order level data isn't paired
        avg_sig = stats.mannwhitneyu(df_KA_o_Var[metric],df_KA_o_Control[metric], alternative='two-sided')[1]
        #avg_sig = stats.wilcoxon(OD_KA[(metric,variant)]/OD_KA[("order",variant)],OD_KA[(metric,"Control")]/OD_KA[("order","Control")], alternative='two-sided')[1]
        avg_sig_tf = avg_sig <= 0.05
      else:
        avg_control = "NA"
        avg_variant = "NA"
        avg_delta= 0
        avg_sig = "NA"
        avg_sig_tf = "NA"
      rows_list.append([metric, variant,sum_control, sum_variant,sum_delta,sum_sig,sum_sig_tf,avg_control,avg_variant,avg_delta,avg_sig, avg_sig_tf])
OD_KA_result = pd.DataFrame(rows_list, columns=['metrics','variant', "sum_control", "sum_variation",'sum_delta','sum_p-value','sum_sig',"avg_control", "avg_variation","avg_delta",'avg_p-value',"avg_sig"])
OD_KA_result['sum_delta'] = OD_KA_result['sum_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
OD_KA_result['avg_delta'] = OD_KA_result['avg_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
OD_KA_result.sort_values(by = ["metrics"])

metrics     variant  sum_control  ...  avg_delta  avg_p-value  avg_sig
6              DF  Variation1     38610.61  ...      2.27%  6.92696e-10     True
2          DF_rev  Variation1     32445.89  ...      2.16%  6.92696e-10     True
3        comm_rev  Variation1     34062.85  ...      0.17%     0.624761    False
7  delivery_costs  Variation1     52555.87  ...     -0.67%     0.498397    False
0           order  Variation1      5839.00  ...      0.00%           NA       NA
4          profit  Variation1     13952.87  ...      7.95%   0.00273036     True
1             rev  Variation1     66508.74  ...      1.14%   0.00712655     True
5     travel_time  Variation1     25405.88  ...     -0.46%     0.460008    False

[8 rows x 12 columns]

### OD excluded only


In [ ]:
# create empty array list
rows_list = []
Variants = ["Variation1"]
metrics = ["order","rev","DF_rev","comm_rev","profit","travel_time","DF","delivery_costs"]

# loop the data for each zone and each stage
for metric in metrics:
  for variant in Variants:
    # create order level data frames for signif. level calculations for KPI averages
      df_excluded_o_Var = df_copy.loc[(df_copy["type"] == "OD_excluded")&(df_copy["variant"] == variant)]
      df_excluded_o_Control = df_copy.loc[(df_copy["type"] == "OD_excluded")&(df_copy["variant"] == "Control")]
      sum_control = round(OD_excluded[(metric,"Control")].sum(),2)
      sum_variant = round(OD_excluded[(metric,variant)].sum(),2)
      sum_delta = sum_variant/sum_control-1   
      sum_sig = stats.wilcoxon(OD_excluded[(metric,variant)], OD_excluded[(metric,"Control")]) [1]/2
      sum_sig_tf = sum_sig <= 0.05
      if metric != "order":
        avg_control = round((OD_excluded[(metric,"Control")].sum()/OD_excluded[("order","Control")].sum()),2)
        avg_variant = round((OD_excluded[(metric,variant)].sum()/OD_excluded[("order",variant)].sum()),2)
        avg_delta = avg_variant/avg_control - 1
        # using non-paired test becasue order level data isn't paired
        avg_sig = stats.mannwhitneyu(df_excluded_o_Var[metric],df_excluded_o_Control[metric], alternative='two-sided')[1]
        #avg_sig = stats.wilcoxon(OD_excluded[(metric,variant)]/OD_excluded[("order",variant)],OD_excluded[(metric,"Control")]/OD_excluded[("order","Control")])[1]/2
        avg_sig_tf = avg_sig <= 0.05
      else:
        avg_control = "NA"
        avg_variant = "NA"
        avg_delta= 0
        avg_sig = "NA"
        avg_sig_tf = "NA"
      rows_list.append([metric, variant,sum_control, sum_variant,sum_delta,sum_sig,sum_sig_tf,avg_control,avg_variant,avg_delta,avg_sig, avg_sig_tf])
OD_excluded_result = pd.DataFrame(rows_list, columns=['metrics','variant', "sum_control", "sum_variation",'sum_delta','sum_p-value','sum_sig',"avg_control", "avg_variation","avg_delta",'avg_p-value',"avg_sig"])
OD_excluded_result['sum_delta'] = OD_excluded_result['sum_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
OD_excluded_result['avg_delta'] = OD_excluded_result['avg_delta'].astype(float).map(lambda n: '{:.2%}'.format(n))
OD_excluded_result.sort_values(by = ["metrics"])

metrics     variant  sum_control  ...  avg_delta avg_p-value  avg_sig
6              DF  Variation1     12919.62  ...      0.69%    0.834272    False
2          DF_rev  Variation1     10856.82  ...      0.83%    0.834272    False
3        comm_rev  Variation1     47501.83  ...      0.19%     0.85594    False
7  delivery_costs  Variation1     50676.46  ...      0.35%    0.411198    False
0           order  Variation1      4492.00  ...      0.00%          NA       NA
4          profit  Variation1      7682.19  ...      0.00%    0.911414    False
1             rev  Variation1     58358.65  ...      0.31%    0.953236    False
5     travel_time  Variation1     29665.33  ...      0.91%    0.282893    False

[8 rows x 12 columns]



```
# This is formatted as code
```

## Deep Dive - Visualization
We look at different metrics:

Economics Metrics
*   Orders
*   Delivery fee
*   Basket value
*   Revenue

Logistics Metrics 

*   Travel Time

In [ ]:
df_od_mp = df_copy.pivot_table(["order","rev","DF","comm_rev","profit","travel_time","delivery_costs",
                                 'rev_sum', 'DF_sum', 'comm_sum', 'profit_sum', 'tt_sum', 'costs_sum',"gfv_sum", "gfv_local"], 
                             index=["local_date", "delivery_type", "variant"], 
                             aggfunc = {"order": "count","rev":"mean","DF":"mean","comm_rev":"mean",
                                        "profit":"mean","travel_time":"mean", "delivery_costs":"mean",  'rev_sum':"sum", 
                                        'DF_sum':"sum", 'comm_sum':"sum", 'profit_sum':"sum",'tt_sum':"sum", 'costs_sum':"sum",
                                        "gfv_sum":"sum", "gfv_local":"mean"}).reset_index()
df_od_mp.head()

local_date delivery_type     variant  ...      rev_sum  travel_time   tt_sum
0 2021-01-27            MP     Control  ...  1529.870000     0.000000     0.00
1 2021-01-27            MP  Variation1  ...  1719.690000     0.000000     0.00
2 2021-01-27            OD     Control  ...  6223.038403     5.030507  2082.63
3 2021-01-27            OD  Variation1  ...  6000.681597     4.751916  1934.03
4 2021-01-28            MP     Control  ...  1758.270000     0.000000     0.00

[5 rows x 18 columns]

In [ ]:
df_od = df_copy.pivot_table(["order","rev","DF","comm_rev","profit","travel_time","delivery_costs",
                                 'rev_sum', 'DF_sum', 'comm_sum', 'profit_sum', 'tt_sum', 'costs_sum',"gfv_sum", "gfv_local"], 
                             index=["local_date", "type", "variant"], 
                             aggfunc = {"order": "count","rev":"mean","DF":"mean","comm_rev":"mean",
                                        "profit":"mean","travel_time":"mean", "delivery_costs":"mean",  'rev_sum':"sum", 
                                        'DF_sum':"sum", 'comm_sum':"sum", 'profit_sum':"sum",'tt_sum':"sum", 'costs_sum':"sum", "gfv_sum":"sum", "gfv_local":"mean"}).reset_index()
df_od.head()

local_date         type     variant  ...      rev_sum  travel_time  tt_sum
0 2021-01-27           MP     Control  ...  1529.870000     0.000000    0.00
1 2021-01-27           MP  Variation1  ...  1719.690000     0.000000    0.00
2 2021-01-27        OD_KA     Control  ...  1239.418235     4.481887  475.08
3 2021-01-27        OD_KA  Variation1  ...  1319.710420     4.315913  496.33
4 2021-01-27  OD_excluded     Control  ...  1207.050840     6.139213  546.39

[5 rows x 18 columns]

### 1. Orders (aggregated level)

#### OD orders

In [ ]:
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="order", color='variant', 
              title = "Total OD order amount in control and test group")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize non-KA orders (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_nonKA'], x="local_date", y="order", color='variant', 
              title = "OD non-KA: order amount in control and test group")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize KA orders (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_KA'], x="local_date", y="order", color='variant', 
              title = "OD KA: order amount in control and test group")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize excluded orders (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_excluded'], x="local_date", y="order", color='variant', 
              title = "OD excluded: order amount in control and test group")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

##### OD - Hour of Day

In [ ]:
# Hour of day level data
order_hour = OD.pivot_table("platform_order_code_ga", index=["new_time"], columns ="variant", aggfunc = "count").reset_index()
order_hour = order_hour.fillna(0)
order_hour["control_pp"] = order_hour["Control"]/order_hour["Control"].sum()
order_hour["variation1_pp"] = order_hour["Variation1"]/order_hour["Variation1"].sum()
#order_hour["variation2_pp"] = order_hour["Variation2"]/order_hour["Variation2"].sum()
order_hour["delta_V1_vs_C"]=order_hour["Variation1"]/order_hour["Control"] -1
#order_hour["delta_V2_vs_C"]=order_hour["Variation2"]/order_hour["Control"] -1

In [ ]:
# visualize Test vs Control orders by hour of day
fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =order_hour.new_time, y=order_hour.control_pp, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =order_hour.new_time, y=order_hour.variation1_pp,name ="variation1"), secondary_y=False)

# Set x-axis title
fig.update_xaxes(title_text="Time")
# Set y-axes titles
fig.update_yaxes(title_text="Order share", showgrid=False, secondary_y=False)
#fig.show()

In [ ]:
fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =order_hour.new_time, y=order_hour.Control, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =order_hour.new_time, y=order_hour.Variation1,name ="variation1"), secondary_y=False)
# Add figure title
#fig.update_layout(title_text="Daily users in Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Time")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

#### MP orders

In [ ]:
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'MP'], x="local_date", y="order", color='variant', 
              title = "MP Order amount in control and test group")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

### Orders (stage level)

In [ ]:
order = df_agg_st.pivot_table("order", index=["local_date", "stage"],aggfunc = "sum").reset_index()
order["all"] = order["Control"] + order["Variation1"]
fig = px.bar(order, x="local_date",y='all', color="stage", category_orders={"stage": ["default", "surge1", "surge2"]})
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False)
fig.show()

/usr/local/lib/python3.7/dist-packages/pandas/core/generic.py:3889: PerformanceWarning:

dropping on a non-lexsorted multi-index without a level parameter may impact performance.



In [ ]:
# surge2 orders
fig = px.line(order[order.stage == 'surge2'], x="local_date", y="Control", #color='variant', 
              title = "orders in control and test group")
fig.add_scatter(x=order[order.stage == 'surge2'].local_date, y=order[order.stage == 'surge2'].Variation1, mode='lines')
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Order amount", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
pivot = df_copy.pivot_table("platform_order_code_ga", index=["stage","new_time","variant"], aggfunc = "count").reset_index()
pivot['platform_order_code_ga_corected'] = pivot.apply (lambda row: row.platform_order_code_ga if row.variant == 'Control' else 
                                                        row.platform_order_code_ga*user_adj_factor_V1, axis = 1)
                                                         #else row.platform_order_code_ga*user_adj_factor_V2

fig = px.bar(pivot, x="new_time", y="platform_order_code_ga_corected", color="stage", 
             #barmode="group",
             #facet_row="variant", 
             facet_col="variant",
             )
fig.show()

### 2. Delivery Fee

#### Total DF

In [ ]:
# visualize OD total DF (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="DF_sum", color='variant', 
              title = "OD: Daily DF of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Total DF", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize non KA total DF (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_nonKA'], x="local_date", y="DF_sum", color='variant', 
              title = "OD non-KA: Daily DF of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="DF", showgrid=False, secondary_y=False)
fig.show()

#### Avg. DF

In [ ]:
# visualize OD avg DF (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="DF", color='variant', 
              title = "OD: Daily avg. DF of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. DF", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize non KA avg DF (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_nonKA'], x="local_date", y="DF", color='variant', 
              title = "OD non-KA: Daily avg. DF of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. DF", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize KA avg DF (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_KA'], x="local_date", y="DF", color='variant', 
              title = "OD KA: Daily avg. DF of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. DF", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize excluded avg DF (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_excluded'], x="local_date", y="DF", color='variant', 
              title = "OD excluded: Daily avg. DF of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. DF", showgrid=False, secondary_y=False)
fig.show()

### 3. Basket Value

In [ ]:
# visualize OD avg GFV (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="gfv_local", color='variant', 
              title = "OD: Daily avg. basket value of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Basket Value", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize non KA avg GFV (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_nonKA'], x="local_date", y="gfv_local", color='variant', 
              title = "OD non-KA: Daily avg. basket value of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Basket Value", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize KA avg GFV (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_KA'], x="local_date", y="gfv_local", color='variant', 
              title = "OD KA: Daily avg. basket value of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Basket Value", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize excluded avg GFV (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_excluded'], x="local_date", y="gfv_local", color='variant', 
              title = "OD excluded: Daily avg. basket value of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Basket Value", showgrid=False, secondary_y=False)
fig.show()

#### Commission Revenue

In [ ]:
# visualize total commission revenue (Control vs Variations)
fig = px.line(df_od_mp, x="local_date", y="comm_sum", color='variant', facet_row = "delivery_type",
              title = "OD: Daily commission revenue of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Commission Revenue", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
df_od_mp.columns

Index(['local_date', 'delivery_type', 'variant', 'DF', 'DF_sum', 'comm_rev',
       'comm_sum', 'costs_sum', 'delivery_costs', 'gfv_local', 'gfv_sum',
       'order', 'profit', 'profit_sum', 'rev', 'rev_sum', 'travel_time',
       'tt_sum'],
      dtype='object')

### 4. Revenue

In [ ]:
df_rev = df_copy.pivot_table(["order","rev", 'rev_sum',  'profit_sum', "profit"], 
                             index=["local_date", "variant"], 
                             aggfunc = {"order": "count","rev":"mean", "profit":"mean",
                                        'rev_sum':"sum", 'profit_sum':"sum"}).reset_index()
df_rev.head()

local_date     variant  order    profit   profit_sum        rev      rev_sum
0 2021-01-27     Control    619  6.110007  3782.094403  12.524892  7752.908403
1 2021-01-27  Variation1    633  5.975837  3782.704597  12.196480  7720.371597
2 2021-01-28     Control    702  5.960306  4184.134588  12.526140  8793.350588
3 2021-01-28  Variation1    703  6.193156  4353.788454  12.487218  8778.514454
4 2021-01-29     Control    775  6.578855  5098.612790  12.614187  9775.994790

#### Total Revenue

In [ ]:
# visualize daily revenue of Test vs Control
fig = px.line(df_rev, x="local_date", y="rev_sum", color='variant', 
              title = "Daily revenue of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Revenue (local currency)", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize OD total revenue (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="rev_sum", color='variant', 
              title = "OD: Daily revenue of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Revenue (local currency)", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize MP total revenue (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'MP'], x="local_date", y="rev_sum", color='variant', 
              title = "MP: Daily revenue of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Revenue (local currency)", showgrid=False, secondary_y=False)
fig.show()

#### Avg. Revenue

In [ ]:
# visualize daily avg. revenue of Test vs Control
fig = px.line(df_rev, x="local_date", y="rev", color='variant', 
              title = "Daily avg. revenue of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Revenue (local currency)", showgrid=False, secondary_y=False)
fig.show()

### 5. Profit

#### Total Profit

In [ ]:
# visualize daily revenue of Test vs Control
fig = px.line(df_rev, x="local_date", y="profit_sum", color='variant', 
              title = "Daily profit of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Profit (local currency)", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize OD total profit (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="profit_sum", color='variant', 
              title = "OD: Daily profit of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Profit (local currency)", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize MP total profit (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'MP'], x="local_date", y="profit_sum", color='variant', 
              title = "MP: Daily profit of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Profit (local currency)", showgrid=False, secondary_y=False)
fig.show()

#### Avg. Profit

In [ ]:
# visualize daily revenue of Test vs Control
fig = px.line(df_rev, x="local_date", y="profit", color='variant', 
              title = "Daily avg. Profit of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Profit (local currency)", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize OD avg. profit (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="profit", color='variant', 
              title = "OD: Daily avg. profit of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Profit (local currency)", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize MP avg. profit (Control vs Variations)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'MP'], x="local_date", y="profit", color='variant', 
              title = "MP: Daily avg. profit of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Profit (local currency)", showgrid=False, secondary_y=False)
fig.show()

### 4. Travel Time

#### Order share

In [ ]:
tt_order = OD.pivot_table("platform_order_code_ga", index=["tt"], columns =["variant","type"], aggfunc = "count").reset_index()

tt_order.columns =[str(s1) + "_" + str(s2) + "_orders" for (s1,s2) in tt_order.columns.tolist()]
tt_order = tt_order.rename(columns={"tt__orders": "tt" })

tt_order["Control_OD_orders"] = tt_order["Control_OD_nonKA_orders"] + tt_order["Control_OD_KA_orders"] + tt_order["Control_OD_excluded_orders"]
tt_order["Variation1_OD_orders"] = tt_order["Variation1_OD_nonKA_orders"] + tt_order["Variation1_OD_KA_orders"] + tt_order["Variation1_OD_excluded_orders"]

tt_order["Control_pp"] = tt_order["Control_OD_orders"]/tt_order["Control_OD_orders"].sum()
tt_order["Variation1_pp"] = tt_order["Variation1_OD_orders"]/tt_order["Variation1_OD_orders"].sum()

tt_order["Control_nonKA_pp"] = tt_order["Control_OD_nonKA_orders"]/tt_order["Control_OD_nonKA_orders"].sum()
tt_order["Variation1_nonKA_pp"] = tt_order["Variation1_OD_nonKA_orders"]/tt_order["Variation1_OD_nonKA_orders"].sum()

tt_order["Control_KA_pp"] = tt_order["Control_OD_KA_orders"]/tt_order["Control_OD_KA_orders"].sum()
tt_order["Variation1_KA_pp"] = tt_order["Variation1_OD_KA_orders"]/tt_order["Variation1_OD_KA_orders"].sum()

tt_order["Control_excluded_pp"] = tt_order["Control_OD_excluded_orders"]/tt_order["Control_OD_excluded_orders"].sum()
tt_order["Variation1_excluded_pp"] = tt_order["Variation1_OD_excluded_orders"]/tt_order["Variation1_OD_excluded_orders"].sum()

tt_order = tt_order.reset_index()
tt_order

index    tt  ...  Control_excluded_pp  Variation1_excluded_pp
0       0   0.0  ...             0.004007                0.006032
1       1   1.0  ...             0.079475                0.060316
2       2   2.0  ...             0.084595                0.101082
3       3   3.0  ...             0.138691                0.134983
4       4   4.0  ...             0.115761                0.099626
5       5   5.0  ...             0.100846                0.094010
6       6   6.0  ...             0.088379                0.099834
7       7   7.0  ...             0.067008                0.076331
8       8   8.0  ...             0.045859                0.049293
9       9   9.0  ...             0.031834                0.033902
10     10  10.0  ...             0.039626                0.047005
11     11  11.0  ...             0.040739                0.037022
12     12  12.0  ...             0.040739                0.048045
13     13  13.0  ...             0.019590                0.014351
14     14  14.0  ...             0.015138                0.011023
15     15  15.0  ...             0.011131                0.017679
16     16  16.0  ...             0.027382                0.022879
17     17  17.0  ...             0.022484                0.014559
18     18  18.0  ...             0.012021                0.018095
19     19  19.0  ...             0.004452                0.004160
20     20  20.0  ...             0.001781                0.000832
21     21  21.0  ...             0.001781                0.002496
22     22  22.0  ...             0.002004                0.002704
23     23  23.0  ...             0.001336                0.000416
24     24  24.0  ...             0.001336                0.002704
25     25  25.0  ...             0.001781                0.000624
26     26  26.0  ...             0.000223                     NaN

[27 rows x 18 columns]

In [ ]:
# visualize distribution across travel time (Control vs Variation 1)
fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Control_pp, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Variation1_pp, name ="variation1"), secondary_y=False)
# Add figure title
fig.update_layout(title_text="Order distribution across travel time")
# Set x-axis title
fig.update_xaxes(title_text="Travel time")
# Set y-axes titles
fig.update_yaxes(title_text="Order share", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize non-KA distribution across travel time (Control vs Variation 1)
fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Control_nonKA_pp, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Variation1_nonKA_pp, name ="variation1"), secondary_y=False)
# Add figure title
fig.update_layout(title_text="Non-KA: Order distribution across travel time")
# Set x-axis title
fig.update_xaxes(title_text="Travel time")
# Set y-axes titles
fig.update_yaxes(title_text="Order share", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize KA distribution across travel time (Control vs Variation 1)
fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Control_KA_pp, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Variation1_KA_pp, name ="variation1"), secondary_y=False)
# Add figure title
fig.update_layout(title_text="KA: Order distribution across travel time")
# Set x-axis title
fig.update_xaxes(title_text="Travel time")
# Set y-axes titles
fig.update_yaxes(title_text="Order share", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize KA distribution across travel time (Control vs Variation 1)
fig = go.Figure()
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Control_excluded_pp, name ="control"), secondary_y=False)
fig.add_trace(go.Bar(x =tt_order.tt, y=tt_order.Variation1_excluded_pp, name ="variation1"), secondary_y=False)
# Add figure title
fig.update_layout(title_text="Excluded vendors: Order distribution across travel time")
# Set x-axis title
fig.update_xaxes(title_text="Travel time")
# Set y-axes titles
fig.update_yaxes(title_text="Order share", showgrid=False, secondary_y=False)
fig.show()

#### avg. TT check

In [ ]:
# visualize avg. travel time (Control vs Variation 1)
fig = px.line(df_od_mp[df_od_mp.delivery_type == 'OD'], x="local_date", y="travel_time", color='variant', 
              title = "OD: Daily avg. Travel Time of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Travel Time", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize non-KA avg. travel time (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_nonKA'], x="local_date", y="travel_time", color='variant', 
              title = "OD nonKA: Daily avg. Travel Time of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Travel Time", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize KA avg. travel time (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_KA'], x="local_date", y="travel_time", color='variant', 
              title = "OD KA: Daily avg. Travel Time of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Travel Time", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
# visualize excluded avg. travel time (Control vs Variation 1)
fig = px.line(df_od[df_od.type == 'OD_excluded'], x="local_date", y="travel_time", color='variant', 
              title = "OD excluded: Daily avg. Travel Time of Control and Test")
# Set x-axis title
fig.update_xaxes(title_text="Date")
# Set y-axes titles
fig.update_yaxes(title_text="Avg. Travel Time", showgrid=False, secondary_y=False)
fig.show()

In [ ]:
fig = px.box(OD, x="variant", y="travel_time")
fig.show()